# 9.2 Introduction to Principal Component Analysis (PCA)

**Principal Component Analysis (PCA)** is a technique used to emphasize variation and bring out strong patterns in a dataset. It's often used to make data easy to explore and visualize or to reduce the number of variables in a dataset while preserving the variation in the dataset as much as possible. It does this by creating new variables called principal components that are linear combinations of the original variables. The first principal component accounts for as much of the variation in the data as possible, and each succeeding component accounts for as much of the remaining variation as possible. PCA is closely related to **singular value decomposition (SVD)**. 

## PCA in a Nutshell

PCA is one of the central applications of the SVD, where we can transform high-dimensional correlated data. In PCA we pre-processes the data by mean subtraction and setting the variance to unity before performing the SVD. The geometry of the resulting coordinate system is determined by principal components (PCs) that are uncorrelated (orthogonal) to each other, but have maximal correlation with the measurements. 

We again consider a dataset of many (real valued) Measurements stored in a matrix $X \in \mathbb{R}^{m \times n}$, where $n$ is the number of measurements and $m$ is the number of features (please note that we changed the dimensions compared to the SVD section). We can write this as:

$$ 
X = \begin{bmatrix}
x_{11} & x_{12} & \dots & x_{1n} \\
x_{21} & x_{22} & \dots & x_{2n} \\
\vdots & \vdots & \ddots & \vdots \\
x_{m1} & x_{m2} & \dots & x_{mn} \\
\end{bmatrix}
$$

where each measurement is $x_i \in \mathbb{R}^m$ and the whole dataset is $X \in \mathbb{R}^{m \times n}$.

First we compute the mean of $X$ for each measurement: 

$$\bar{x}_j = \frac{1}{n}\sum_{i=1}^n x_ij$$

and construct the mean Matrix $X_M$:

$$X_M = \begin{bmatrix}
\bar{x}_1 & \bar{x}_2 & \dots & \bar{x}_n \\
\bar{x}_1 & \bar{x}_2 & \dots & \bar{x}_n \\
\vdots & \vdots & \ddots & \vdots \\
\bar{x}_1 & \bar{x}_2 & \dots & \bar{x}_n \\
\end{bmatrix}$$

Then we subtract the mean from each measurement resulting in the mean substracted data $B$:

$$B = \frac{1}{\sqrt{n-1}} (X - X_M)^T$$

Using the mean subtracted data $B$ we compute the covariance matrix of $B$:

$$C_X = B^TB$$

The principal components of $X$ are also the eigenvectors of $C_X$. Hence, if we calculate the SVD of $X$, the columns of matrix $V$ contain the eigenvectors of $B^TB = C_X$ (see the description of $V$ in the SVD section). Therefore, the columns of $V$ are the principal components of $X$. 

In summary we can write the following pseudo code for PCA:

```python
# PCA - Perform PCA using SVD.
# Input: data - MxN matrix of input data (M dimensions, N trials)
[M,N] = size(data)
mean_x = mean(X, axis=2)
data = data - repmat(mean_x,1,N)
B = data* / sqrt(N-1)
[u,S,PC] = svd(B)

# calculate the variances
S = diag(S)
V = S .* S

# project the original data
signals = PC’ * data
```

## Example: Measuring a spring-mass system using cameras

We will use an example from "A Tutorial on Principal Component Analyses" by Jonathon Shlens (https://arxiv.org/pdf/1404.1100.pdf) to illustrate the use of PCA. 

Consider the following example. We have an ideal spring-mass system of a ball with mass m attached to a massless, frictionless spring. The spring is attached to a wall and the ball is free to move in the horizontal direction. The ball is initially at rest at the equilibrium position of the spring. We then pull the ball to the right and release it. The ball will then oscillate back and forth. We are interested in measuring the position of the mass over time. We have three video cameras which we can use to track the position of the mass (see figure below).

![Spring-mass system](spring_mass_system.png)

Since we do not know anything about the system, we did not position the cameras in a position which would allow us to directly measure the position of the mass. Instead, we positioned the cameras in arbitrary angles. By doing this we can only measure the position of the mass in the x- and y-directions of each camera frame. Hence we want to use the measured camera positions to calculate the position of the mass in its x-direction. How do we get from this data set to a simple equation of x?

First let start with the problem and the data.


In [ ]:
import Pkg
Pkg.instantiate()

In [ ]:
import Pkg
# # Pkg.generate("PCA")
Pkg.activate("PCA")
Pkg.add("Revise")
Pkg.add("Plots")
Pkg.add("LinearAlgebra")
Pkg.add("Statistics")
Pkg.add("Random")
Pkg.add("Revise")

In [ ]:
import Pkg
Pkg.activate("PCA")
using Revise
include("./SpringMass.jl") # this file implements the generation of our spring-mass toy problem 
using .SpringMass
using Statistics, LinearAlgebra, Random, Plots

Let's generate our dataset and take a first look at it:

In [ ]:
amplitude = 2.0 # amplitude of the motion
X, x_true, y_true = generate_dataset(amplitude)

So what do we have here? 

The dataset X is a matrix where each row corresponds to a different time step and each column corresponds to a different measurement. The measurements are the x and y coordinates of the ball's position as recorded by three different cameras. The cameras are not aligned with the true x and y axes, but instead have their own coordinate systems that are rotated at arbitrary angles with respect to the true axes.

Before we take a look at the data we plot the true motion of the ball we want to measure. This will give us an idea what we expect to see in the data.

In [ ]:
# Plot the "true" motion
p = plot(x_true, label="True Motion", title="True Motion of the Ball", xlabel="Time", ylabel="x")

Now let's take a look at the data. We have three cameras which measure the position of the ball in the x- and y-directions. We can plot the position of the ball in the x- and y-directions for each camera:

In [ ]:
# Scatter Plot the 2-dim data
p1 = scatter(X[:, 1], X[:, 2], label="Camera 1")
p2 = scatter(X[:, 3], X[:, 4], label="Camera 2")
p3 = scatter(X[:, 5], X[:, 6], label="Camera 3")
plot(p1, p2, p3, title="Scatter Plot of Data", xlabel="x", ylabel="y")

Here's a breakdown of the columns in X:
- Columns 1 and 2: The x and y coordinates of the ball's position as recorded by camera 1 (Plot 1).
- Columns 3 and 4: The x and y coordinates of the ball's position as recorded by camera 2 (Plot 2).
- Columns 5 and 6: The x and y coordinates of the ball's position as recorded by camera 3 (Plot 3).

So these 6 columns are the measurements we have. Where each measurement $x_{i}$ at time step $i$ can be viewed as: 

$$
x_{i} = \begin{bmatrix}
x_{a} \\
y_{a} \\
x_{b} \\
y_{b} \\
x_{c} \\
y_{c} 
\end{bmatrix}
$$

Each row in X represents a different time step $i$. The time steps are evenly spaced and cover the entire duration of the ball's motion. We simulated for 10 seconds with a time step of 0.01 seconds, so there are 1000 rows in X.

The values in X are real numbers that represent the position of the ball in the coordinate system of each camera. These values have been corrupted by Gaussian noise to simulate measurement error.

In order to analyze this dataset, we will perform Principal Component Analysis (PCA) to find the directions of greatest variance in the data. These directions, known as the principal components, can reveal the true motion of the ball, as well as the relationships between the different measurements.

## PCA on the spring-mass system 
Now let us compute the principal components of our data set. We will preprocess the data and use the ```eigen()``` function od the LinearAlgebra package to compute the principal components as explained above. 

In [ ]:
# Perform PCA
μ = mean(X, dims=1)  # compute the mean
X_centered = X .- μ  # center the data
Σ = X_centered' * X_centered / (size(X, 1) - 1)  # compute the covariance matrix
λ, V = eigen(Σ)  # compute the eigenvalues and eigenvectors

In [ ]:
# The principal components are given by the eigenvectors
PCs = V

In [ ]:
# Plot the original data and the principal components
p1 = plot(X, label=["Camera 1 x" "Camera 1 y" "Camera 2 x" "Camera 2 y" "Camera 3 x" "Camera 3 y"], title="Original Data")
p2 = plot(X * PCs, label=["PC 1" "PC 2" "PC 3" "PC 4" "PC 5" "PC 6"], title="Principal Components")
plot(p1, p2, layout=(1, 2), size=(1200, 400), legend=:topleft)

### Things we can do with PCA

1. Correlation: If your data variables are correlated, PCA can help identify these correlations. Highly correlated variables will contribute to the same principal component.

2. Dimensionality Reduction: If your data has many dimensions, PCA can be used to reduce its dimensionality while preserving as much of the data's variation as possible. The reduced-dimension data can be easier to analyze and visualize.

3. Variance Explained: The eigenvalues of the covariance matrix in PCA represent the amount of variance explained by each principal component. The first principal component explains the most variance, the second principal component explains the second most, and so on. By examining these eigenvalues, you can get a sense of how much of the total variance in your data is captured by each principal component.

4. Outlier Detection: Outliers are observations that are far from the main cluster of data points. PCA can help detect outliers by looking at the principal components that explain the most variance. Outliers will often show up as extreme values on the principal components.

In [ ]:
# combine the transformed data into a matrix
X_projected = X * PCs

In [ ]:
# Scatter Plot the 2-dim data
p1 = scatter(X_projected[:, 1], X_projected[:, 2], label="Projected Data PC 1 and 2") 
p2 = scatter(X_projected[:, 3], X_projected[:, 4], label="Projected Data PC 3 and 4")
p3 = scatter(X_projected[:, 5], X_projected[:, 6], label="Projected Data PC 5 and 6")
plot(p1, p2, p3, title="Scatter Plot of Data", xlabel="x", ylabel="y")


**Correlation** We can already see that the data is highly correlated when we look at the scatter plots of the data and compate this to the transformed data. We can also see this by looking at the correlation matrix of the data: 

In [ ]:
# correlation matrix of our data
cor(X)

We can also look at the correlation matrix of the data transformed by PCA:

In [ ]:
# correlation matrix of the transformed data
cor(X_projected)

**Dimensionality Reduction** We can reduce the two dimensional data to one dimension using PCA. This is done by projecting the data onto the first principal component as we have done above.

In [ ]:
reduced_data = X_projected[:, end] # reduce the data to one dimension

# Plot the reduced data
plot(reduced_data, label="Projected Data", title="Data Projected onto First Principal Component", ylabel="Values of the First Principal Component")

We can actually see that we are able to retrieve the true motion of the ball by looking at the first principal component. The first principal component is a linear combination of the original measurements. We can see the coefficients of this linear combination by looking at the first row of the matrix V. We are actually able to do this since the ball is moving in a straight line. If the ball was moving in a more complicated way, we would not be able to recover the true motion of the ball by looking at the first principal component, since the first principal component is a linear combination of the original measurements. 

**Variance Explained:** We can combine the explained variance with the data to see how much of the variance in the data is explained by each principal component. 

In [ ]:
# Compute the variance explained by each principal component
var_explained = λ ./ sum(λ)

println("Variance explained by each principal component: ", var_explained)

# Plot the variance explained
p1 = bar(1:length(var_explained), var_explained, title="Variance Explained by Each Principal Component", xlabel="Principal Component", ylabel="Var. Explained")

# Plot the projected data
p2 = plot(X_projected[:, end], label="Projected Data", title="Data Projected onto First Principal Component", ylabel="First PC")

p3 = plot(X_projected[:, 1:end-1], label="Projected Data", title="Data Projected onto First Principal Component", ylabel="Other PCs")

# Display the plots
plot(p1, p2, p3, layout=(3, 1))

## Task 1: Spring Mass with more noise in the data

Now let's take a look at what happens when we increase the amount of noise in the data. We will increase the standard deviation of the noise from 0.25 to 2.0. This will make the data much more noisy and harder to analyze. This noise could be viewed as inaccurate measurements for example by chaking of the cameras. Load the following data set and see what the PCA tells you about the system: 

In [ ]:
amplitude = 2.0 # amplitude of the motion
noise_level = 2.0 # noise level of the data, this can be viewed as chaking of the cameras
X, x_true, y_true = generate_dataset(amplitude, noise_level)

In [ ]:
# Scatter Plot the 2-dim data
p1 = scatter(X[:, 1], X[:, 2], label="Camera 1")
p2 = scatter(X[:, 3], X[:, 4], label="Camera 2")
p3 = scatter(X[:, 5], X[:, 6], label="Camera 3")
plot(p1, p2, p3, title="Scatter Plot of Data", xlabel="x", ylabel="y")

## Task 2: Spring Mass with deviations in the y direction

Now the mass is released off-center so as to produce motion in the $y$ plane as well as the $x$ direction. Load the following data set and see what the PCA tells you about the system: 

In [ ]:
amplitude = 2.0 # amplitude of the motion
noise_level = 0.25 # noise level of the data, this can be viewed as chaking of the cameras
amplitude_deviation = 1.0 # deviation in the y direction
X, x_true, y_true = generate_dataset(amplitude, noise_level, amplitude_deviation)

In [ ]:
# Scatter Plot the 2-dim data
p1 = scatter(X[:, 1], X[:, 2], label="Camera 1")
p2 = scatter(X[:, 3], X[:, 4], label="Camera 2")
p3 = scatter(X[:, 5], X[:, 6], label="Camera 3")
plot(p1, p2, p3, title="Scatter Plot of Data", xlabel="x", ylabel="y")